# Laplacian Eigenmaps for Dimensionality Reduction

### Dr. Juan Orduz

In this notebook we present some simple examples which ilustrate the concepts discussed in the talk on [Laplacian Eigenmaps for Dimensionality Reduction](https://pydata.org/berlin2018/schedule/presentation/33/) at [PyData Berlin 2018](https://pydata.org/berlin2018/).

The sample data and object descriptions can be found in the documentation.

**References:**

- http://scikit-learn.org/stable/modules/generated/sklearn.manifold.spectral_embedding.html

- http://scikit-learn.org/stable/modules/manifold.html#spectral-embedding

## 1. Notebook Setup

In [1]:
import numpy as np
from sklearn import manifold, datasets
from sklearn.utils import check_random_state
from sklearn.decomposition import PCA

from IPython.display import Image
from IPython.core.display import HTML 

# Visualization with Plotly.
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import cufflinks as cf
import plotly.graph_objs as go
init_notebook_mode(connected=True)
cf.go_offline()

## 2. Back to Our Toy Example

![toy_graph](toy_graph.png)

In [2]:
# Construct the adjacency matrix from the graph for n_neighbors = 1. 
W = np.array([[0, 1, 1, 1],
              [1, 0, 0, 0], 
              [1, 0, 0, 0], 
              [1, 0, 0, 0]])

# Construct the degree matrix D from W.
D = np.diag(np.apply_along_axis(arr=W,
                                func1d=np.sum,
                                axis=0))
# Compute the graph Laplcian.
L = D - W

print(L)

[[ 3 -1 -1 -1]
 [-1  1  0  0]
 [-1  0  1  0]
 [-1  0  0  1]]


Let us use `manifold.spectral_embedding` to compute the projection onto $\mathbb{R}$.

In [3]:
y = manifold.spectral_embedding(adjacency=W, 
                                n_components=1, 
                                norm_laplacian=False, 
                                drop_first=True,
                                eigen_solver='lobpcg')

print(y)

[[ 0.        ]
 [-0.57735027]
 [ 0.78867513]
 [-0.21132487]]


Let us verify the result. Recall that the first non zero eigenvalue of is 1. 

In [4]:
lambda_1 = 1

np.array_equal(a1=np.dot(L, y), 
               a2=lambda_1*np.dot(D, y))

True

Thus, $y$ is a solution of $Lf = \lambda_1 Df$ with $\lambda_1 =1$.

## 3 Higher Dimensional Examples

###  3.1 S Curve

**Reference:** http://scikit-learn.org/stable/modules/generated/sklearn.datasets.make_s_curve.html

In [5]:
# Define the number of points to cosider. 
n_points = 3000

# Get the data and color map. 
S_curve, S_colors = datasets.samples_generator.make_s_curve(n_points, random_state=0)

# Define parameters for the Scatter3d plot. 
trace_S_curve = go.Scatter3d(
                    x=S_curve[:, 0],
                    y=S_curve[:, 1],
                    z=S_curve[:, 2],
                    mode='markers',
                    marker=dict(
                        size=6,
                        color = S_colors,
                        colorscale='Rainbow',
                        opacity=0.8
    )
)

layout = go.Layout(
            margin=dict(
                l=0,
                r=0,
                b=0,
                t=0
    )
)

# Generate plot. 
iplot(go.Figure(data=[trace_S_curve], layout=layout))

#### 3.1.1 PCA

In [6]:
# Fit PCA object.
S_curve_pca = PCA(n_components=2).fit_transform(S_curve)

# Visualize the result.
trace_S_curve_pca = go.Scatter(
                        x=S_curve_pca[:, 0],
                        y=S_curve_pca[:, 1],
                        mode='markers',
                        marker=dict(
                            size=6,
                            color = S_colors,
                            colorscale='Rainbow',
                            opacity=0.8
    )
)

iplot(go.Figure(data=[trace_S_curve_pca], layout=layout))

#### 3.1.2 Spectral Embedding

In [7]:
# Set the number of n_neighbors;
n_neighbors = 6 # Try 1500

# Set the dimension of the target space. 
n_components = 2

# Construct the SpectralEmbedding object. 
se = manifold.SpectralEmbedding(n_components=n_components,
                                affinity= 'nearest_neighbors',
                                n_neighbors=n_neighbors)

# Fit the SpectralEmbedding object. 
S_curve_red = se.fit_transform(X=S_curve)

In [8]:
# Visualize the result.
trace_S_curve_red = go.Scatter(
                        x=S_curve_red[:, 0],
                        y=S_curve_red[:, 1],
                        mode='markers',
                        marker=dict(
                            size=6,
                            color = S_colors,
                            colorscale='Rainbow',
                            opacity=0.8
    )
)

iplot(go.Figure(data=[trace_S_curve_red], layout=layout))

### 3.2 Two Dimensional Sphere $S^2$

**Reference:** http://scikit-learn.org/stable/auto_examples/manifold/plot_manifold_sphere.html

First we generate the data.

In [9]:
# Create our sphere.
n_samples = 3000

angle_parameter = 0.5 # Try 0.01
pole_hole_parameter = 8 # Try 50

random_state = check_random_state(0)
p = random_state.rand(n_samples) * (2 * np.pi - angle_parameter)
t = random_state.rand(n_samples) * np.pi

# Sever the poles from the sphere.
indices = ((t < (np.pi - (np.pi / pole_hole_parameter))) & (t > ((np.pi / pole_hole_parameter))))
colors = p[indices]
x, y, z = np.sin(t[indices]) * np.cos(p[indices]), \
          np.sin(t[indices]) * np.sin(p[indices]), \
          np.cos(t[indices])
        
sphere_data = np.array([x, y, z]).T

Let us visualize the data.

In [10]:
trace_sphere = go.Scatter3d(
                    x=x,
                    y=y,
                    z=z,
                    mode='markers',
                    marker=dict(
                        size=6,
                        color = colors,
                        colorscale='Rainbow',
                        opacity=0.8
    )
)

iplot(go.Figure(data=[trace_sphere], layout=layout))

#### 3.2.1 PCA

In [11]:
sphere_pca = PCA(n_components=2).fit_transform(sphere_data)

trace_S_curve_pca = go.Scatter(
                        x=sphere_pca[:, 0],
                        y=sphere_pca[:, 1],
                        mode='markers',
                        marker=dict(
                            size=6,
                            color = S_colors,
                            colorscale='Rainbow',
                            opacity=0.8
    )
)

iplot(go.Figure(data=[trace_S_curve_pca], layout=layout))

#### 3.3.2 Spectral Embedding

In [12]:
n_neighbors = 6 # Try 1000
n_components = 2

# Fit the object.
se = manifold.SpectralEmbedding(n_components=n_components,
                                affinity='nearest_neighbors',
                                n_neighbors=n_neighbors)

sphere_data_red = se.fit_transform(X=sphere_data)

Let us visualize the results.

In [13]:
trace_sphere_data = go.Scatter(
                        x=sphere_data_red[:, 0],
                        y=sphere_data_red[:, 1],
                        mode='markers',
                        marker=dict(
                            size=6,
                            color = colors,
                            colorscale='Rainbow',
                            opacity=0.8
    )
)


iplot(go.Figure(data=[trace_sphere_data], layout=layout))